In [1]:
gameId = "doapp"
#gameId = "sfiii3n"
#gameId = "tektagt"

In [2]:
import sys, os
import time
timeDepSeed = int((time.time()-int(time.time()-0.5))*1000)

sys.path.append(os.path.join(os.path.abspath(''), '../'))   
sys.path.append(os.path.join(os.path.abspath(''), '../../../games'))   

tensorBoardFolder = "./{}_ppo2_TB_CustCnnSmall_bL_d_noComb/".format(gameId)
modelFolder = "./{}_ppo2_Model_CustCnnSmall_bL_d_noComb/".format(gameId)

os.makedirs(modelFolder, exist_ok=True)

In [3]:
from makeDiambraEnv import *

import tensorflow as tf

from customPolicies.utils import linear_schedule, AutoSave
from customPolicies.customCnnPolicy import *

from stable_baselines import PPO2

In [4]:
# Diambra environment kwargs
diambraKwargs = {}
diambraKwargs["roms_path"]   = "../../../roms/mame/"
diambraKwargs["binary_path"] = "../../../customMAME/"
diambraKwargs["frame_ratio"] = 6
diambraKwargs["render"]      = False

diambraKwargs["player"] = "Random" # P1 / P2

# Game dependent kwawrgs
if gameId == "doapp":
    diambraKwargs["difficulty"]  = 3 
    diambraKwargs["characters"] =["Kasumi", "Kasumi"]
    diambraKwargs["charOutfits"] =[2, 2]
elif gameId == "sfiii3n":
    diambraKwargs["difficulty"]  = 6
    diambraKwargs["characters"] =["Ryu", "Ryu"]
    diambraKwargs["charOutfits"] =[2, 2]
elif gameId == "tektagt":
    diambraKwargs["difficulty"]  = 6
    diambraKwargs["characters"] =[["Jin", "Yoshimitsu"], ["Jin", "Yoshimitsu"]]
    diambraKwargs["charOutfits"] =[2, 2]
else:
    raise Exception("Game not implemented: {}".format(gameId))

# DIAMBRA gym kwargs
diambraGymKwargs = {}
diambraGymKwargs["P2brain"] = None
diambraGymKwargs["continue_game"] = 0.0 # If < 0.0 means number of continues
diambraGymKwargs["show_final"] = False
diambraGymKwargs["gamePads"] = [None, None]                                     
diambraGymKwargs["actionSpace"] = ["discrete", "discrete"]
diambraGymKwargs["attackButCombinations"] = [False, False]

# Gym Wrappers kwargs
wrapperKwargs = {}
wrapperKwargs["hwc_obs_resize"] = [128, 128, 1]
wrapperKwargs["normalize_rewards"] = True
wrapperKwargs["clip_rewards"] = False
wrapperKwargs["frame_stack"] = 4
wrapperKwargs["dilation"] = 1
wrapperKwargs["scale"] = True
wrapperKwargs["scale_mod"] = 0

# Additional observations
keyToAdd = []
keyToAdd.append("actionsBuf") # env.actBufLen*(env.n_actions[0]+env.n_actions[1])

if gameId != "tektagt":                                                         
    keyToAdd.append("ownHealth")   # 1                                            
    keyToAdd.append("oppHealth")   # 1                                                
else:                                                                           
    keyToAdd.append("ownHealth_1") # 1                                             
    keyToAdd.append("ownHealth_2") # 1                                             
    keyToAdd.append("oppHealth_1") # 1                                              
    keyToAdd.append("oppHealth_2") # 1  
    
keyToAdd.append("ownPosition")     # 1
keyToAdd.append("oppPosition")     # 1
keyToAdd.append("stage")           # 1
keyToAdd.append("character")       # len(env.charNames)

numEnv=8

envId = gameId + "_Train"
env = make_diambra_env(diambraMame, env_prefix=envId, num_env=numEnv, seed=timeDepSeed, 
                       diambra_kwargs=diambraKwargs, diambra_gym_kwargs=diambraGymKwargs,
                       wrapper_kwargs=wrapperKwargs, key_to_add=keyToAdd, use_subprocess=True)

In [5]:
print("Obs_space = ", env.observation_space)
print("Obs_space type = ", env.observation_space.dtype)
print("Obs_space high = ", env.observation_space.high)
print("Obs_space low = ", env.observation_space.low)

Obs_space =  Box(128, 128, 5)
Obs_space type =  float32
Obs_space high =  [[[1. 1. 1. 1. 1.]
  [1. 1. 1. 1. 1.]
  [1. 1. 1. 1. 1.]
  ...
  [1. 1. 1. 1. 1.]
  [1. 1. 1. 1. 1.]
  [1. 1. 1. 1. 1.]]

 [[1. 1. 1. 1. 1.]
  [1. 1. 1. 1. 1.]
  [1. 1. 1. 1. 1.]
  ...
  [1. 1. 1. 1. 1.]
  [1. 1. 1. 1. 1.]
  [1. 1. 1. 1. 1.]]

 [[1. 1. 1. 1. 1.]
  [1. 1. 1. 1. 1.]
  [1. 1. 1. 1. 1.]
  ...
  [1. 1. 1. 1. 1.]
  [1. 1. 1. 1. 1.]
  [1. 1. 1. 1. 1.]]

 ...

 [[1. 1. 1. 1. 1.]
  [1. 1. 1. 1. 1.]
  [1. 1. 1. 1. 1.]
  ...
  [1. 1. 1. 1. 1.]
  [1. 1. 1. 1. 1.]
  [1. 1. 1. 1. 1.]]

 [[1. 1. 1. 1. 1.]
  [1. 1. 1. 1. 1.]
  [1. 1. 1. 1. 1.]
  ...
  [1. 1. 1. 1. 1.]
  [1. 1. 1. 1. 1.]
  [1. 1. 1. 1. 1.]]

 [[1. 1. 1. 1. 1.]
  [1. 1. 1. 1. 1.]
  [1. 1. 1. 1. 1.]
  ...
  [1. 1. 1. 1. 1.]
  [1. 1. 1. 1. 1.]
  [1. 1. 1. 1. 1.]]]
Obs_space low =  [[[0. 0. 0. 0. 0.]
  [0. 0. 0. 0. 0.]
  [0. 0. 0. 0. 0.]
  ...
  [0. 0. 0. 0. 0.]
  [0. 0. 0. 0. 0.]
  [0. 0. 0. 0. 0.]]

 [[0. 0. 0. 0. 0.]
  [0. 0. 0. 0. 0.]
  [0. 0. 0.

In [6]:
print("Act_space = ", env.action_space)
print("Act_space type = ", env.action_space.dtype)
if diambraGymKwargs["actionSpace"][0] == "multiDiscrete":
    print("Act_space n = ", env.action_space.nvec)
else:
    print("Act_space n = ", env.action_space.n)

Act_space =  Discrete(12)
Act_space type =  int64
Act_space n =  12


In [7]:
# Policy param
n_actions = env.get_attr("n_actions")[0][0]
actBufLen = env.get_attr("actBufLen")[0]

policyKwargs={}
policyKwargs["n_add_info"] = actBufLen*(n_actions[0]+n_actions[1]) + len(keyToAdd)-2 # No Char Info
policyKwargs["layers"] = [64, 64]

policyKwargs["cnn_extractor"] = local_nature_cnn_small

print("n_add_info =", policyKwargs["n_add_info"])

n_add_info = 161


In [8]:
# PPO param
setGamma = 0.94
#setLearningRate = linear_schedule(2.5e-4, 2.5e-6)
setLearningRate = linear_schedule(5.0e-5, 2.5e-6)
#setClipRange = linear_schedule(0.15, 0.025)
setClipRange = linear_schedule(0.075, 0.025)
setClipRangeVf = setClipRange

# Initialize the model
#model = PPO2(CustCnnPolicy, env, verbose=1, 
#             gamma = setGamma, nminibatches=4, noptepochs=4, n_steps=128,
#             learning_rate=setLearningRate, cliprange=setClipRange, cliprange_vf=setClipRangeVf, 
#             tensorboard_log=tensorBoardFolder, policy_kwargs=policyKwargs)

#OR

# Load the trained agent
model = PPO2.load(os.path.join(modelFolder, "9M"), env=env, tensorboard_log=tensorBoardFolder, 
                  policy_kwargs=policyKwargs, gamma = setGamma, learning_rate=setLearningRate, 
                  cliprange=setClipRange, cliprange_vf=setClipRangeVf)





Instructions for updating:
Use keras.layers.flatten instead.

Instructions for updating:
Use tf.where in 2.0, which has the same broadcast rule as np.where




In [9]:
print("Model discount factor = ", model.gamma)

Model discount factor =  0.94


In [10]:
# Create the callback: autosave every USER DEF steps
autoSaveCallback = AutoSave(check_freq=1000000, numEnv=numEnv, save_path=os.path.join(modelFolder,"9M_"))

# Train the agent
time_steps = 10000000
model.learn(total_timesteps=time_steps, callback=autoSaveCallback)


------------------------------------
| approxkl           | 0.00426923  |
| clipfrac           | 0.20751953  |
| explained_variance | 0.06        |
| fps                | 26          |
| n_updates          | 1           |
| policy_entropy     | 0.88678503  |
| policy_loss        | -0.01932368 |
| serial_timesteps   | 128         |
| time_elapsed       | 1.81e-05    |
| total_timesteps    | 1024        |
| value_loss         | 0.010165044 |
------------------------------------
-------------------------------------
| approxkl           | 0.003013378  |
| clipfrac           | 0.15942383   |
| explained_variance | 0.21         |
| fps                | 17           |
| n_updates          | 2            |
| policy_entropy     | 0.93708044   |
| policy_loss        | -0.017537028 |
| serial_timesteps   | 256          |
| time_elapsed       | 38.7         |
| total_timesteps    | 2048         |
| value_loss         | 0.011756372  |
-------------------------------------
------------------------

-------------------------------------
| approxkl           | 0.0045799464 |
| clipfrac           | 0.18041992   |
| ep_len_mean        | 1.59e+03     |
| ep_reward_mean     | 7.31         |
| explained_variance | 0.224        |
| fps                | 22           |
| n_updates          | 17           |
| policy_entropy     | 0.99847054   |
| policy_loss        | -0.020290244 |
| serial_timesteps   | 2176         |
| time_elapsed       | 784          |
| total_timesteps    | 17408        |
| value_loss         | 0.014672257  |
-------------------------------------
-------------------------------------
| approxkl           | 0.003667084  |
| clipfrac           | 0.16503906   |
| ep_len_mean        | 1.73e+03     |
| ep_reward_mean     | 8.36         |
| explained_variance | 0.365        |
| fps                | 22           |
| n_updates          | 18           |
| policy_entropy     | 1.010736     |
| policy_loss        | -0.019184848 |
| serial_timesteps   | 2304         |
| time_elaps

------------------------------------
| approxkl           | 0.004605165 |
| clipfrac           | 0.16821289  |
| ep_len_mean        | 1.73e+03    |
| ep_reward_mean     | 8.35        |
| explained_variance | 0.241       |
| fps                | 23          |
| n_updates          | 32          |
| policy_entropy     | 0.9842754   |
| policy_loss        | -0.0179162  |
| serial_timesteps   | 4096        |
| time_elapsed       | 1.56e+03    |
| total_timesteps    | 32768       |
| value_loss         | 0.013510818 |
------------------------------------
-------------------------------------
| approxkl           | 0.0042171413 |
| clipfrac           | 0.16748047   |
| ep_len_mean        | 1.73e+03     |
| ep_reward_mean     | 8.35         |
| explained_variance | 0.189        |
| fps                | 19           |
| n_updates          | 33           |
| policy_entropy     | 1.0791131    |
| policy_loss        | -0.019431151 |
| serial_timesteps   | 4224         |
| time_elapsed       | 1.6e

-------------------------------------
| approxkl           | 0.0040550316 |
| clipfrac           | 0.17138672   |
| ep_len_mean        | 1.72e+03     |
| ep_reward_mean     | 8.19         |
| explained_variance | 0.251        |
| fps                | 17           |
| n_updates          | 47           |
| policy_entropy     | 1.1070333    |
| policy_loss        | -0.019369029 |
| serial_timesteps   | 6016         |
| time_elapsed       | 2.31e+03     |
| total_timesteps    | 48128        |
| value_loss         | 0.017121304  |
-------------------------------------
-------------------------------------
| approxkl           | 0.0038258699 |
| clipfrac           | 0.17700195   |
| ep_len_mean        | 1.76e+03     |
| ep_reward_mean     | 8.17         |
| explained_variance | 0.433        |
| fps                | 27           |
| n_updates          | 48           |
| policy_entropy     | 1.1233966    |
| policy_loss        | -0.019089127 |
| serial_timesteps   | 6144         |
| time_elaps

-------------------------------------
| approxkl           | 0.0049095326 |
| clipfrac           | 0.17504883   |
| ep_len_mean        | 1.75e+03     |
| ep_reward_mean     | 8.01         |
| explained_variance | 0.261        |
| fps                | 20           |
| n_updates          | 62           |
| policy_entropy     | 0.9927826    |
| policy_loss        | -0.01906894  |
| serial_timesteps   | 7936         |
| time_elapsed       | 3.05e+03     |
| total_timesteps    | 63488        |
| value_loss         | 0.01511311   |
-------------------------------------
-------------------------------------
| approxkl           | 0.0050865146 |
| clipfrac           | 0.16040039   |
| ep_len_mean        | 1.73e+03     |
| ep_reward_mean     | 8.03         |
| explained_variance | 0.425        |
| fps                | 15           |
| n_updates          | 63           |
| policy_entropy     | 1.0460634    |
| policy_loss        | -0.019804543 |
| serial_timesteps   | 8064         |
| time_elaps

...

--------------------------------------
| approxkl           | 0.00031782463 |
| clipfrac           | 0.0859375     |
| ep_len_mean        | 1.84e+03      |
| ep_reward_mean     | 9.1           |
| explained_variance | 0.267         |
| fps                | 17            |
| n_updates          | 7875          |
| policy_entropy     | 0.9512945     |
| policy_loss        | -0.0059308223 |
| serial_timesteps   | 1008000       |
| time_elapsed       | 4.16e+05      |
| total_timesteps    | 8064000       |
| value_loss         | 0.013386124   |
--------------------------------------
--------------------------------------
| approxkl           | 0.00027391026 |
| clipfrac           | 0.08496094    |
| ep_len_mean        | 1.84e+03      |
| ep_reward_mean     | 9.1           |
| explained_variance | 0.236         |
| fps                | 15            |
| n_updates          | 7876          |
| policy_entropy     | 1.0415751     |
| policy_loss        | -0.0063014845 |
| serial_timesteps   | 10

--------------------------------------
| approxkl           | 0.00026388423 |
| clipfrac           | 0.08276367    |
| ep_len_mean        | 1.85e+03      |
| ep_reward_mean     | 9.08          |
| explained_variance | 0.257         |
| fps                | 17            |
| n_updates          | 7890          |
| policy_entropy     | 1.103787      |
| policy_loss        | -0.006756778  |
| serial_timesteps   | 1009920       |
| time_elapsed       | 4.17e+05      |
| total_timesteps    | 8079360       |
| value_loss         | 0.01564249    |
--------------------------------------
--------------------------------------
| approxkl           | 0.00023069845 |
| clipfrac           | 0.0769043     |
| ep_len_mean        | 1.84e+03      |
| ep_reward_mean     | 9.06          |
| explained_variance | 0.2           |
| fps                | 14            |
| n_updates          | 7891          |
| policy_entropy     | 1.0668836     |
| policy_loss        | -0.0063038403 |
| serial_timesteps   | 10

-------------------------------------
| approxkl           | 0.0002649161 |
| clipfrac           | 0.0859375    |
| ep_len_mean        | 1.86e+03     |
| ep_reward_mean     | 9.3          |
| explained_variance | 0.183        |
| fps                | 16           |
| n_updates          | 7905         |
| policy_entropy     | 1.08411      |
| policy_loss        | -0.006737143 |
| serial_timesteps   | 1011840      |
| time_elapsed       | 4.17e+05     |
| total_timesteps    | 8094720      |
| value_loss         | 0.015991122  |
-------------------------------------
--------------------------------------
| approxkl           | 0.00026764523 |
| clipfrac           | 0.08251953    |
| ep_len_mean        | 1.86e+03      |
| ep_reward_mean     | 9.3           |
| explained_variance | 0.153         |
| fps                | 25            |
| n_updates          | 7906          |
| policy_entropy     | 1.0731618     |
| policy_loss        | -0.006267405  |
| serial_timesteps   | 1011968       |
|

--------------------------------------
| approxkl           | 0.00029199902 |
| clipfrac           | 0.09277344    |
| ep_len_mean        | 1.89e+03      |
| ep_reward_mean     | 9.51          |
| explained_variance | 0.263         |
| fps                | 20            |
| n_updates          | 7920          |
| policy_entropy     | 1.0578107     |
| policy_loss        | -0.0066087595 |
| serial_timesteps   | 1013760       |
| time_elapsed       | 4.18e+05      |
| total_timesteps    | 8110080       |
| value_loss         | 0.015480762   |
--------------------------------------
--------------------------------------
| approxkl           | 0.00027495698 |
| clipfrac           | 0.09326172    |
| ep_len_mean        | 1.89e+03      |
| ep_reward_mean     | 9.5           |
| explained_variance | 0.285         |
| fps                | 15            |
| n_updates          | 7921          |
| policy_entropy     | 1.0618575     |
| policy_loss        | -0.007038337  |
| serial_timesteps   | 10

KeyboardInterrupt: 

In [11]:
# Save the agent
model.save(os.path.join(modelFolder, "19M"))

## Evaluation

In [ ]:
# Initialize a new evaluation environment
diambraKwargs["render"] = True

envId = gameId + "_Test"
env = make_diambra_env(diambraMame, env_prefix=envId, num_env=1, seed=timeDepSeed, 
                       diambra_kwargs=diambraKwargs, diambra_gym_kwargs=diambraGymKwargs,
                       wrapper_kwargs=wrapperKwargs, key_to_add=keyToAdd)

In [ ]:
observation = env.reset()

cumulativeEpRew = 0.0
cumulativeEpRewAll = []

maxNumEp = 10
currNumEp = 0

while currNumEp < maxNumEp:

    action = model.predict(observation, deterministic=True)
    #action_prob = model.action_probability(observation, states)
    #print("Action probabilities = ", action_prob)
    #print("Max action = ", np.argmax(action_prob))
    #print("Action = ", action)
    
    observation, reward, done, info = env.step(action[0])
    
    cumulativeEpRew += reward
    
    if np.any(done):
        currNumEp += 1
        print("Ep. # = ", currNumEp)
        print("Ep. Cumulative Rew # = ", cumulativeEpRew)
        cumulativeEpRewAll.append(cumulativeEpRew)
        cumulativeTotRew += cumulativeEpRew
        cumulativeEpRew = 0.0
    
env.close()

In [ ]:
print("Cumulative reward = ", cumulativeEpRewAll)    
print("Mean cumulative reward = ", np.mean(cumulativeEpRewAll))    
print("Std cumulative reward = ", np.std(cumulativeEpRewAll))  